<a href="https://colab.research.google.com/github/eeyamazaki/gps_tracking/blob/main/gps_tracking.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [343]:
pip install movingpandas

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [344]:
pip install keplergl

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [345]:
pip install dbfread

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [4]:
# import csv
# from dbfread import DBF

# def dbf_to_csv(dbf_table_pth):#Input a dbf, output a csv, same name, same path, except extension
#     csv_fn = dbf_table_pth[:-4]+ ".csv" #Set the csv file name
#     table = DBF(dbf_table_pth, encoding='utf-8')# table variable is a DBF object
#     with open(csv_fn, 'w', newline = '') as f:# create a csv file, fill it with dbf content
#         writer = csv.writer(f)
#         writer.writerow(table.field_names)# write the column name
#         for record in table:# write the rows
#             writer.writerow(list(record.values()))
#     return csv_fn# return the csv name


# dbf_to_csv(r'/content/drive/MyDrive/Projetos/gps_tracking/data/Ligacoes/Export_Output.dbf')

In [346]:
# Instalar e Importar bibliotecas necessarias

import pandas as pd
import geopandas as gpd
import movingpandas as mpd
from shapely.geometry import Point
from pyproj import CRS
from keplergl import KeplerGl
from datetime import datetime, timedelta

In [347]:
dfLigacoes = pd.read_csv(r'/content/drive/MyDrive/Projetos/gps_tracking/data/Ligacoes/Export_Output.csv')
dfLigacoes.head()

OBJECTID         ID        RGI  SUBLOCAL CATEGORIA_  CODIGO_COM  \
0         1   50919325  577375253       0.0      Comum       916.0   
1         2   50913618  577375334       0.0      Comum       916.0   
2         3  161904463  577375415       0.0      Comum       916.0   
3         4  160299020  577375687       0.0      Comum       916.0   
4         5  156507111  577375768       0.0      Comum       916.0   

                        INSERIDO_P   NUM_HIDRO  VILA  DATA_INSTA  ...  \
0       root@Administrador@gis_155  Y19T784638   0.0  2020-03-03  ...   
1       root@Administrador@gis_155   SEM HIDRO   0.0  2017-09-16  ...   
2  root_gerenciadora@Administrador  Y09T066292   0.0  2009-03-16  ...   
3  root_gerenciadora@Administrador   SEM HIDRO   0.0  2017-04-07  ...   
4  root_gerenciadora@Administrador  Y19T232520   0.0  2019-05-30  ...   

    IMOVEL  CRIADO_AUT STATUS COORD_UTM_  COORD_UTM1 COTA_VERTI      POINT_X  \
0    430.0         Sim      R        0.0         0.0      779.0  335011.1894   
1   3010.0         NaN      E        0.0         0.0      732.0  334121.6696   
2    269.0         Não      M        0.0         0.0      789.0  335421.6905   
3  19465.0         Sim      E        0.0         0.0      822.0  338704.1929   
4      4.0         Não      R        0.0         0.0      740.0  337566.6926   

        POINT_Y          X          Y  
0  7.405238e+06 -46.615249 -23.454514  
1  7.399663e+06 -46.624571 -23.504768  
2  7.402637e+06 -46.611517 -23.478041  
3  7.410962e+06 -46.578491 -23.403203  
4  7.405511e+06 -46.590209 -23.452308  

[5 rows x 37 columns]

In [348]:
dfLigacoes = dfLigacoes.drop(['OBJECTID', 'ID', 'SUBLOCAL', 'CATEGORIA_', 'CODIGO_COM', 'INSERIDO_P', 'NUM_HIDRO', 'VILA', 'DATA_INSTA', 'DATA_INSER', 'TL',
                        'ACTUALIZAD', 'NUMERO_SAB', 'RE_HISTORI', 'CATEGORIA1', 'SETOR', 'ROTA', 'ULTIMA_ACT', 'LOCAL', 'CODIGO_MUN', 'QUADRA',
                        'COMPLEMENT', 'AGRUPAMENT', 'TRATA_ESGO', 'CODLOG', 'CRIADO_AUT', 'STATUS', 'COORD_UTM_', 'COORD_UTM1', 'COTA_VERTI',
                        'POINT_X', 'POINT_Y', 'ENDERECO_C', 'IMOVEL'], axis=1)

In [349]:
import glob

path = r'/content/drive/MyDrive/Projetos/gps_tracking/data/Servicos/Vila Maria'
filenames = glob.glob(path + "/*.xlsx")

dfs = []
for filename in filenames:
  dfs.append(pd.read_excel(filename, dtype=object))

dfVila = pd.concat(dfs, ignore_index=True)
dfVila.head()

/usr/local/lib/python3.7/dist-packages/openpyxl/styles/stylesheet.py:226: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")


Unidade Executante         Id  Número OS Etapa  \
0  MNT - UG REGIONAL SANTANA  1345646.0  215200505         
1  MNT - UG REGIONAL SANTANA  1346280.0  215203679         
2  MNT - UG REGIONAL SANTANA  1348589.0  215211453         
3  MNT - UG REGIONAL SANTANA  1351880.0  215233357         
4  MNT - UG REGIONAL SANTANA  1356010.0  215284577         

                           Fornecimento - Titular  Município  \
0  230359787001 - JOAO HENRIQUE ALVES DE OLIVEIRA  SÃO PAULO   
1            230833101001 - ALISSON BATISTA ROSSI  SÃO PAULO   
2       681239301002 - SERGIO MARTINS DE OLIVEIRA  SÃO PAULO   
3           86040379395671 - JOSE MARIO DOS ANJOS  SÃO PAULO   
4                    86040379435077 - ROBERTO GIL  SÃO PAULO   

                                            Endereço          Iniciativa  \
0   RUA ANIBAL AUGUSTO SARDINHA, 189,  - V NILO -...  INICIATIVA CLIENTE   
1   RUA LIBERO DE MIRANDA, 119,  - JACANA - SÃO P...  INICIATIVA CLIENTE   
2   AVENIDA DOUTOR BENEDITO ESTEVAM SANTOS, 1324,...  INICIATIVA CLIENTE   
3   RUA JOSE GONCALVES GOMIDE, 30, AP 173 - V GUI...  INICIATIVA CLIENTE   
4   RUA MOREIRA DE VASCONCELOS, 351,  - V MARIA -...  INICIATIVA CLIENTE   

      Data Inserção Data de Competência  ... Status da Operação  \
0  15/10/2021 12:50    15/10/2021 12:50  ...            Fechada   
1  15/10/2021 13:26    15/10/2021 13:25  ...            Fechada   
2  15/10/2021 14:50    15/10/2021 14:49  ...            Fechada   
3  15/10/2021 17:37    15/10/2021 17:37  ...            Fechada   
4  16/10/2021 10:02    16/10/2021 10:02  ...            Fechada   

  Data Fim Execução Origem OS                                     TSS  \
0  11/11/2021 15:47       SIU  APROVAR MODIFICAÇÃO DE LIGAÇÃO DE AGUA   
1  01/11/2021 10:07       SIU  VERIFICAR EXISTENCIA LIG ESGOTO AVULSA   
2  01/11/2021 10:16       SIU  VERIFICAR EXISTENCIA LIGAÇÃO DE ESGOTO   
3  16/11/2021 13:59       SIU               APROVAR LIGAÇÃO DE ESGOTO   
4  16/11/2021 14:05       SIU                 APROVAR LIGAÇÃO DE AGUA   

     Família      Formulário de Baixa               Fornecedor    Contrato  \
0  APROVAÇÃO  LIGAÇÃO DE AGUA APROV 3                   SABESP  9999999999   
1   VISTORIA                      NaN                   SABESP  9999999999   
2   VISTORIA                      NaN                   SABESP  9999999999   
3  APROVAÇÃO                      NaN  CONSÓRCIO TACE SF NORTE  4600024658   
4  APROVAÇÃO                      NaN  CONSÓRCIO TACE SF NORTE  4600024658   

                    Causa Resultado Notificação de Esgoto  
0  TROCAR CAVALETE POR UMA APROVADO                   NaN  
1         TRATA-SE DE OUTRO SERVIÇO                   NaN  
2         TRATA-SE DE OUTRO SERVIÇO                   NaN  
3              NADA CONSTA NO LOCAL                   NaN  
4              NADA CONSTA NO LOCAL                   NaN  

[5 rows x 24 columns]

In [350]:
dfVila = dfVila.drop_duplicates(['Id'])

In [351]:
dfVila = dfVila.drop(['Unidade Executante', 'Id', 'Etapa', 'Município', 'Iniciativa',
             'Data Inserção', 'Data Inserção','Prazo de Execução - Início', 'Prazo de Execução - Fim', 'Tempo Residual',
             'Status da OS','Status da Operação', 'Origem OS', 'Família', 'Formulário de Baixa', 'Contrato', 'Notificação de Esgoto'], axis=1)

In [352]:
print(dfVila['Fornecedor'].unique())

['SABESP' 'CONSÓRCIO TACE SF NORTE' 'CONSORCIO VISTORIA NORTE'
 'CONSÓRCIO NOVA NORTE II' 'CONSORCIO NOVA NORTE VIII'
 'TECSA SERVIÇOS LTDA.' nan 'CONSORCIO FRESACAPA SOEBE - ERA'
 'CONSÓRCIO C.A.S.E. - SANTANA']


In [353]:
mask = dfVila['Fornecedor']=='TECSA SERVIÇOS LTDA.'

In [354]:
# Filtrando o Fornecedor

dfVila = dfVila[mask]

In [355]:
# Filtrando o TSS

print(dfVila['TSS'].unique())

['DESOBSTRUIR REDE DE ESGOTO' 'DESOBSTRUIR RAMAL DE ESGOTO'
 'DESOBSTRUIR RETORNO PARA IMOVEL'
 'APOIO A EQUIPES DE MANUTENÇÃO DE ESGOTO'
 'LAVAR REDE DE ESGOTO PREVENTIVA' 'LIMPAR POÇO INSPEÇÃO/VISITA A VACUO'
 'DESCOBRIR VALVULA DE REDE DE AGUA' 'INSPECIONAR REDE DE ESGOTO'
 'TESTE DE FUMAÇA' 'LAVAR REDE DE ESGOTO'
 'APROVAR MODIFICAÇÃO DE LIGAÇÃO DE ESGOTO' 'INSPECIONAR RAMAL DE ESGOTO'
 'LIGAÇÃO DE ÁGUA DIMENSIONADA S/V.' 'VISTORIA LIGAÇÃO INATIVA SEM DÉBITO'
 'FALTA DE ÁGUA GERAL']


In [356]:
# Filtrando o TSS

mask = dfVila['TSS']=='DESOBSTRUIR REDE DE ESGOTO'
dfVila = dfVila[mask]

In [357]:
dfVila.head()

Número OS                             Fornecimento - Titular  \
164  217120589                235219029001 - MONICA ROTONDO RAMOS   
168  217120890  233181989001 - ALICE CORDEIRO DE FIGUEIREDO RE...   
176  217126188   235150908001 - QUITERIA MACEDO OLIVEIRA DA SILVA   
179  217127075                     239727770001 - CLEODON MARTINS   
198  217139178              239023455003 - VIACAO SANTA CRUZ LTDA   

                                              Endereço Data de Competência  \
164    RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO    01/11/2021 06:56   
168      RUA TANQUE VELHO, 2093,  - V NIVI - SÃO PAULO    01/11/2021 07:03   
176          RUA PRINCIPAL, 65,  - V MARIA - SÃO PAULO    01/11/2021 08:23   
179   RUA JOAO LUIS BOZZI, 260,  - PQ EDU CHAVES - ...    01/11/2021 08:33   
198   RUA EUGENIO DE FREITAS, 777,  - V GUILHERME -...    01/11/2021 10:08   

    Data Fim Execução                         TSS            Fornecedor  \
164  01/11/2021 14:35  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
168  01/11/2021 08:55  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
176  01/11/2021 09:50  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
179  01/11/2021 08:55  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
198  01/11/2021 10:45  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   

                 Causa Resultado  
164  DESOBSTRUIDA REDE DE ESGOTO  
168  DESOBSTRUIDA REDE DE ESGOTO  
176         NADA CONSTA NO LOCAL  
179                  DUPLICIDADE  
198         NADA CONSTA NO LOCAL

In [358]:
#Splitando a coluna de fornecimento para extrair apenas os codigos:

dfVila['Fornecimento - Titular'] = [x.split(' -')[-0] for x in dfVila['Fornecimento - Titular']]

In [359]:
dfVila.columns

Index(['Número OS', 'Fornecimento - Titular', 'Endereço',
       'Data de Competência', 'Data Fim Execução', 'TSS', 'Fornecedor',
       'Causa Resultado'],
      dtype='object')

In [360]:
dfVila.head()

Número OS Fornecimento - Titular  \
164  217120589           235219029001   
168  217120890           233181989001   
176  217126188           235150908001   
179  217127075           239727770001   
198  217139178           239023455003   

                                              Endereço Data de Competência  \
164    RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO    01/11/2021 06:56   
168      RUA TANQUE VELHO, 2093,  - V NIVI - SÃO PAULO    01/11/2021 07:03   
176          RUA PRINCIPAL, 65,  - V MARIA - SÃO PAULO    01/11/2021 08:23   
179   RUA JOAO LUIS BOZZI, 260,  - PQ EDU CHAVES - ...    01/11/2021 08:33   
198   RUA EUGENIO DE FREITAS, 777,  - V GUILHERME -...    01/11/2021 10:08   

    Data Fim Execução                         TSS            Fornecedor  \
164  01/11/2021 14:35  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
168  01/11/2021 08:55  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
176  01/11/2021 09:50  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
179  01/11/2021 08:55  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
198  01/11/2021 10:45  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   

                 Causa Resultado  
164  DESOBSTRUIDA REDE DE ESGOTO  
168  DESOBSTRUIDA REDE DE ESGOTO  
176         NADA CONSTA NO LOCAL  
179                  DUPLICIDADE  
198         NADA CONSTA NO LOCAL

In [361]:
dfVila.rename(columns={'Número OS': 'os', 'Fornecimento - Titular':'fornecimento', 'Endereço':'endereco',
                       'Data de Competência':'data_competencia', 'Data Fim Execução':'data_execucao',
                       'TSS':'tss', 'Fornecedor':'fornecedor', 'Causa Resultado':'causa_resultado'}, inplace=True)

In [362]:
# Lendo a tabela de cadastros:

dfFornecimento = pd.read_csv(r'/content/drive/MyDrive/Projetos/gps_tracking/data/Fornecimento/cadastro_noduplicates.csv', sep=',', dtype=object) 

In [363]:
dfFornecimento = dfFornecimento.drop(['Unnamed: 0', 'refer', 'sujeito', 'ATC', 'ugr',
       'UN', 'diretoria', 'setor', 'rota', 'quadra', 'local', 'vila',
       'sublocal', 'cdSetaba', 'cdSistProd', 'codlog', 'nr', 'compl', 'bairro',
       'cep', 'hidro', 'Categoria', 'TL', 'mercado', 'produto', 'grupo',
       'ciclo', 'utilizacao', 'tpFornecimento', 'tpSujeito', 'stPDE',
       'stFornecimento', 'SITE', 'SITA', 'situacao', 'tpBenef', 'dtfimben',
       'dtligagua', 'dtligesgo', 'codramo', 'RES', 'COM', 'IND', 'pub',
       'dtinst'], axis=1)

In [364]:
dfFornecimento.head()

pde  fornecimento
0   98059076   98059076001
1  104693894  104693894001
2  230688500  230688500001
3  405900627  405900627005
4  407152725  407152725002

In [365]:
dfVila.head()

os  fornecimento  \
164  217120589  235219029001   
168  217120890  233181989001   
176  217126188  235150908001   
179  217127075  239727770001   
198  217139178  239023455003   

                                              endereco  data_competencia  \
164    RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO  01/11/2021 06:56   
168      RUA TANQUE VELHO, 2093,  - V NIVI - SÃO PAULO  01/11/2021 07:03   
176          RUA PRINCIPAL, 65,  - V MARIA - SÃO PAULO  01/11/2021 08:23   
179   RUA JOAO LUIS BOZZI, 260,  - PQ EDU CHAVES - ...  01/11/2021 08:33   
198   RUA EUGENIO DE FREITAS, 777,  - V GUILHERME -...  01/11/2021 10:08   

        data_execucao                         tss            fornecedor  \
164  01/11/2021 14:35  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
168  01/11/2021 08:55  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
176  01/11/2021 09:50  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
179  01/11/2021 08:55  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   
198  01/11/2021 10:45  DESOBSTRUIR REDE DE ESGOTO  TECSA SERVIÇOS LTDA.   

                 causa_resultado  
164  DESOBSTRUIDA REDE DE ESGOTO  
168  DESOBSTRUIDA REDE DE ESGOTO  
176         NADA CONSTA NO LOCAL  
179                  DUPLICIDADE  
198         NADA CONSTA NO LOCAL

In [366]:
dfVila.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2526 entries, 164 to 61904
Data columns (total 8 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   os                2526 non-null   object
 1   fornecimento      2526 non-null   object
 2   endereco          2526 non-null   object
 3   data_competencia  2526 non-null   object
 4   data_execucao     2526 non-null   object
 5   tss               2526 non-null   object
 6   fornecedor        2526 non-null   object
 7   causa_resultado   2526 non-null   object
dtypes: object(8)
memory usage: 177.6+ KB


In [367]:
dfFornecimento.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 305978 entries, 0 to 305977
Data columns (total 2 columns):
 #   Column        Non-Null Count   Dtype 
---  ------        --------------   ----- 
 0   pde           305978 non-null  object
 1   fornecimento  305977 non-null  object
dtypes: object(2)
memory usage: 4.7+ MB


In [368]:
# Merging a tabela de servicos com o fornecimento para obter o pde:

dfServicos = pd.merge(dfVila, dfFornecimento)
dfServicos.head()

os  fornecimento                                          endereco  \
0   217120589  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
1  2213857848  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
2  2228054536  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
3  2228500845  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
4   217120890  233181989001     RUA TANQUE VELHO, 2093,  - V NIVI - SÃO PAULO   

   data_competencia     data_execucao                         tss  \
0  01/11/2021 06:56  01/11/2021 14:35  DESOBSTRUIR REDE DE ESGOTO   
1  22/04/2022 09:10  23/04/2022 08:19  DESOBSTRUIR REDE DE ESGOTO   
2  23/08/2022 09:40  24/08/2022 08:20  DESOBSTRUIR REDE DE ESGOTO   
3  26/08/2022 13:53  26/08/2022 16:00  DESOBSTRUIR REDE DE ESGOTO   
4  01/11/2021 07:03  01/11/2021 08:55  DESOBSTRUIR REDE DE ESGOTO   

             fornecedor              causa_resultado        pde  
0  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  235219029  
1  TECSA SERVIÇOS LTDA.    TRATA-SE DE OUTRO SERVIÇO  235219029  
2  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  235219029  
3  TECSA SERVIÇOS LTDA.    TRATA-SE DE OUTRO SERVIÇO  235219029  
4  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  233181989

In [369]:
# Renomeando as variaveis:

dfLigacoes.rename(columns={'RGI':'pde', 'X':'latitude', 'Y':'longitude'}, inplace=True)

In [370]:
dfServicos.head()

os  fornecimento                                          endereco  \
0   217120589  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
1  2213857848  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
2  2228054536  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
3  2228500845  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
4   217120890  233181989001     RUA TANQUE VELHO, 2093,  - V NIVI - SÃO PAULO   

   data_competencia     data_execucao                         tss  \
0  01/11/2021 06:56  01/11/2021 14:35  DESOBSTRUIR REDE DE ESGOTO   
1  22/04/2022 09:10  23/04/2022 08:19  DESOBSTRUIR REDE DE ESGOTO   
2  23/08/2022 09:40  24/08/2022 08:20  DESOBSTRUIR REDE DE ESGOTO   
3  26/08/2022 13:53  26/08/2022 16:00  DESOBSTRUIR REDE DE ESGOTO   
4  01/11/2021 07:03  01/11/2021 08:55  DESOBSTRUIR REDE DE ESGOTO   

             fornecedor              causa_resultado        pde  
0  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  235219029  
1  TECSA SERVIÇOS LTDA.    TRATA-SE DE OUTRO SERVIÇO  235219029  
2  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  235219029  
3  TECSA SERVIÇOS LTDA.    TRATA-SE DE OUTRO SERVIÇO  235219029  
4  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  233181989

In [371]:
# Convertendo as variaveis 'pde' antes do merge:

dfServicos['pde'] = dfServicos['pde'].astype(int)
dfLigacoes['pde'] = dfLigacoes['pde'].astype(int)

In [372]:
# Merging da tabela de servicos com a tabela de latitude e longitude das ligacoes:

#Inner join, apenas servicos correspondentes.

dfServicos = pd.merge(dfServicos, dfLigacoes)

In [373]:
dfServicos.head()

os  fornecimento                                          endereco  \
0   217120589  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
1  2213857848  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
2  2228054536  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
3  2228500845  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
4   217120890  233181989001     RUA TANQUE VELHO, 2093,  - V NIVI - SÃO PAULO   

   data_competencia     data_execucao                         tss  \
0  01/11/2021 06:56  01/11/2021 14:35  DESOBSTRUIR REDE DE ESGOTO   
1  22/04/2022 09:10  23/04/2022 08:19  DESOBSTRUIR REDE DE ESGOTO   
2  23/08/2022 09:40  24/08/2022 08:20  DESOBSTRUIR REDE DE ESGOTO   
3  26/08/2022 13:53  26/08/2022 16:00  DESOBSTRUIR REDE DE ESGOTO   
4  01/11/2021 07:03  01/11/2021 08:55  DESOBSTRUIR REDE DE ESGOTO   

             fornecedor              causa_resultado        pde  latitude  \
0  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  235219029 -46.57382   
1  TECSA SERVIÇOS LTDA.    TRATA-SE DE OUTRO SERVIÇO  235219029 -46.57382   
2  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  235219029 -46.57382   
3  TECSA SERVIÇOS LTDA.    TRATA-SE DE OUTRO SERVIÇO  235219029 -46.57382   
4  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  233181989 -46.58537   

   longitude  
0 -23.516436  
1 -23.516436  
2 -23.516436  
3 -23.516436  
4 -23.473747

In [374]:
# Lendo os arquivos de registro do GPS:

path = r'/content/drive/MyDrive/Projetos/gps_tracking/data/Registros'
filenames = glob.glob(path + "/*.xlsx")

dfs = []
for filename in filenames:
  dfs.append(pd.read_excel(filename, dtype=object))

data = pd.concat(dfs, ignore_index=True)
data.head()

Última Comunicação            Data GPS Km/h Velocidade Via Odômetro  \
0 2022-09-26 11:16:06 2022-09-26 11:16:06   23             40    10656   
1 2022-09-26 11:14:06 2022-09-26 11:14:06   26             40    10655   
2 2022-09-26 11:12:06 2022-09-26 11:12:06    0             40    10655   
3 2022-09-26 11:12:06 2022-09-26 11:12:06    0             40    10655   
4 2022-09-26 11:10:06 2022-09-26 11:10:06   30             40    10654   

  Ignição  UF     Cidade                      Endereço    Nº   Latitude  \
0  Ligada  SP  São Paulo   Travessa Figueiredo Camargo  3466 -23.494971   
1  Ligada  SP  São Paulo  Rua Padre Sabóia de Medeiros    19 -23.500789   
2  Ligada  SP  São Paulo      Avenida Alberto Byington  1210 -23.504437   
3  Ligada  SP  São Paulo      Avenida Alberto Byington  1210 -23.504437   
4  Ligada  SP  São Paulo                 Rua Orindiúva   122 -23.506641   

   Longitude Sinal Modem  
0 -46.584656         Bom  
1 -46.589687      Máximo  
2  -46.59187      Máximo  
3  -46.59187      Máximo  
4 -46.587784      Máximo

In [375]:
# Verificando os registros duplicados:

len(data['Última Comunicação'])-len(data['Última Comunicação'].drop_duplicates())

7413

In [376]:
# Dropando os valores duplicados:

data.drop_duplicates(subset=['Última Comunicação'], inplace=True)

In [377]:
data.head()

Última Comunicação            Data GPS Km/h Velocidade Via Odômetro  \
0 2022-09-26 11:16:06 2022-09-26 11:16:06   23             40    10656   
1 2022-09-26 11:14:06 2022-09-26 11:14:06   26             40    10655   
2 2022-09-26 11:12:06 2022-09-26 11:12:06    0             40    10655   
4 2022-09-26 11:10:06 2022-09-26 11:10:06   30             40    10654   
5 2022-09-26 11:08:06 2022-09-26 11:08:06    0             40    10654   

  Ignição  UF     Cidade                      Endereço    Nº   Latitude  \
0  Ligada  SP  São Paulo   Travessa Figueiredo Camargo  3466 -23.494971   
1  Ligada  SP  São Paulo  Rua Padre Sabóia de Medeiros    19 -23.500789   
2  Ligada  SP  São Paulo      Avenida Alberto Byington  1210 -23.504437   
4  Ligada  SP  São Paulo                 Rua Orindiúva   122 -23.506641   
5  Ligada  SP  São Paulo            Rua Gastão Madeira   429 -23.506134   

   Longitude Sinal Modem  
0 -46.584656         Bom  
1 -46.589687      Máximo  
2  -46.59187      Máximo  
4 -46.587784      Máximo  
5 -46.583785      Máximo

In [378]:
# Renomeando o df
data = data.rename(columns={'Última Comunicação':'UltimaComunicacao', 'Data GPS':'DataGPS', 'Km/h':'Velocidade',
                    'Velocidade Via':'VelocidadeVia', 'Odômetro':'Odometro', 'Ignição':'Ignicao', 'Endereço':'Endereco',
                    'Nº':'Num', 'Sinal Modem':'SinalModem'})

In [379]:
# Reordenando as coordenadas por ordem de sinal da ultima comunicacao:

data = data.sort_values(by=['UltimaComunicacao'], ascending=True)

In [380]:
# Criando a variavel com pontos geometricos

data['geometry'] = [Point(long, lat) for long, lat in zip(data['Longitude'].to_list(), data['Latitude'].to_list())]

/usr/local/lib/python3.7/dist-packages/pandas/core/dtypes/cast.py:118: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  arr = construct_1d_object_array_from_listlike(values)


In [381]:
geodata =gpd.GeoDataFrame(data, crs = CRS.from_epsg('4326'))

In [382]:
geodata.head()

UltimaComunicacao             DataGPS Velocidade VelocidadeVia  \
9571 2022-08-22 00:00:47 2022-08-22 00:00:47          0            40   
9570 2022-08-22 00:00:52 2022-08-22 00:00:52          0            40   
9569 2022-08-22 00:00:56 2022-08-22 00:00:56          0            40   
9568 2022-08-22 00:22:32 2022-08-22 00:22:32          0            40   
9567 2022-08-22 01:02:52 2022-08-22 01:02:52          0            40   

     Odometro    Ignicao  UF     Cidade     Endereco  Num  Latitude  \
9571     9506  Desligada  SP  São Paulo  Rua Prainha  227 -23.50948   
9570     9506  Desligada  SP  São Paulo  Rua Prainha  227 -23.50948   
9569     9506  Desligada  SP  São Paulo  Rua Prainha  227 -23.50948   
9568     9506  Desligada  SP  São Paulo  Rua Prainha  227 -23.50948   
9567     9506  Desligada  SP  São Paulo  Rua Prainha  227 -23.50948   

      Longitude SinalModem                     geometry  
9571 -46.585132     Máximo  POINT (-46.58513 -23.50948)  
9570 -46.585132     Máximo  POINT (-46.58513 -23.50948)  
9569 -46.585132     Máximo  POINT (-46.58513 -23.50948)  
9568 -46.585132     Máximo  POINT (-46.58513 -23.50948)  
9567 -46.585132     Máximo  POINT (-46.58513 -23.50948)

In [383]:
# Criando um timestamp

geodata['t'] = pd.to_datetime(geodata['UltimaComunicacao']).dt.tz_localize(None)

In [384]:
# Timestamp como index

geodata = geodata.set_index('t')
geodata.head()

UltimaComunicacao             DataGPS Velocidade  \
t                                                                        
2022-08-22 00:00:47 2022-08-22 00:00:47 2022-08-22 00:00:47          0   
2022-08-22 00:00:52 2022-08-22 00:00:52 2022-08-22 00:00:52          0   
2022-08-22 00:00:56 2022-08-22 00:00:56 2022-08-22 00:00:56          0   
2022-08-22 00:22:32 2022-08-22 00:22:32 2022-08-22 00:22:32          0   
2022-08-22 01:02:52 2022-08-22 01:02:52 2022-08-22 01:02:52          0   

                    VelocidadeVia Odometro    Ignicao  UF     Cidade  \
t                                                                      
2022-08-22 00:00:47            40     9506  Desligada  SP  São Paulo   
2022-08-22 00:00:52            40     9506  Desligada  SP  São Paulo   
2022-08-22 00:00:56            40     9506  Desligada  SP  São Paulo   
2022-08-22 00:22:32            40     9506  Desligada  SP  São Paulo   
2022-08-22 01:02:52            40     9506  Desligada  SP  São Paulo   

                        Endereco  Num  Latitude  Longitude SinalModem  \
t                                                                       
2022-08-22 00:00:47  Rua Prainha  227 -23.50948 -46.585132     Máximo   
2022-08-22 00:00:52  Rua Prainha  227 -23.50948 -46.585132     Máximo   
2022-08-22 00:00:56  Rua Prainha  227 -23.50948 -46.585132     Máximo   
2022-08-22 00:22:32  Rua Prainha  227 -23.50948 -46.585132     Máximo   
2022-08-22 01:02:52  Rua Prainha  227 -23.50948 -46.585132     Máximo   

                                        geometry  
t                                                 
2022-08-22 00:00:47  POINT (-46.58513 -23.50948)  
2022-08-22 00:00:52  POINT (-46.58513 -23.50948)  
2022-08-22 00:00:56  POINT (-46.58513 -23.50948)  
2022-08-22 00:22:32  POINT (-46.58513 -23.50948)  
2022-08-22 01:02:52  POINT (-46.58513 -23.50948)

In [385]:
# Criando a variavel do caminhao

geodata['caminhao'] = 'VilaMaria'

In [386]:
# Criando a variavel de colecao de trajetorias com o mvp

traj_collection = mpd.TrajectoryCollection(geodata, 'caminhao')

In [387]:
# Definindo os parametros para o algoritmo de parada.
# Variavel Hours em 'horas' e Search Radio em 'm'.

Hours = 0.25
SearchRadio = 200

# Deteccao de parada
stops = mpd.TrajectoryStopDetector(traj_collection).get_stop_segments(min_duration=timedelta(hours=Hours), 
                                                                      max_diameter=SearchRadio)

In [388]:
# Criando um novo geodataframe e definindo a variavel geometrica

stops_start = gpd.GeoDataFrame(columns=['geometry'])
stops_start = stops_start.set_geometry('geometry')

In [389]:
# Adicionando o ID de cada parada no caminho e definindo como index

stops_start['stop_id'] = [track.id for track in stops.trajectories]
stops_start = stops_start.set_index('stop_id')

In [390]:
stops_start.head()

geometry
stop_id                               
VilaMaria_2022-08-22 00:00:47     None
VilaMaria_2022-08-22 09:10:12     None
VilaMaria_2022-08-22 09:36:12     None
VilaMaria_2022-08-22 10:24:12     None
VilaMaria_2022-08-22 12:24:12     None

In [391]:
# Iterando pelas paradas no caminho

for stoptrack in stops.trajectories:
    
    #adicionando a duracao de parada em 'h'
    stops_start.at[stoptrack.id, 'duration_h'] = stoptrack.get_duration().total_seconds()/3600
    
    #adicionando a distancia percorrida em 'm'
    stops_start.at[stoptrack.id, 'length_m'] = stoptrack.get_length()
    
    #identificando o caminhao
    stops_start.at[stoptrack.id, 'caminhao'] = stoptrack.id.split('_')[0]
    
    #adicionando a data
    stops_start.at[stoptrack.id, 'datetime'] = stoptrack.id.split('_')[1]
    
    #adicionando o ponto de partida
    stops_start.at[stoptrack.id, 'geometry'] = stoptrack.get_start_location()

stops_start.head()

geometry  duration_h  \
stop_id                                                                  
VilaMaria_2022-08-22 00:00:47  POINT (-46.58513 -23.50948)    8.856944   
VilaMaria_2022-08-22 09:10:12  POINT (-46.57843 -23.47650)    0.333333   
VilaMaria_2022-08-22 09:36:12  POINT (-46.58046 -23.46450)    0.366667   
VilaMaria_2022-08-22 10:24:12  POINT (-46.59782 -23.50340)    1.333333   
VilaMaria_2022-08-22 12:24:12  POINT (-46.56525 -23.52028)    0.733333   

                                 length_m   caminhao             datetime  
stop_id                                                                    
VilaMaria_2022-08-22 00:00:47   15.492745  VilaMaria  2022-08-22 00:00:47  
VilaMaria_2022-08-22 09:10:12   23.836020  VilaMaria  2022-08-22 09:10:12  
VilaMaria_2022-08-22 09:36:12  214.530951  VilaMaria  2022-08-22 09:36:12  
VilaMaria_2022-08-22 10:24:12  289.900227  VilaMaria  2022-08-22 10:24:12  
VilaMaria_2022-08-22 12:24:12  104.641575  VilaMaria  2022-08-22 12:24:12

In [392]:
path = '/content/drive/MyDrive/Projetos/gps_tracking/data/stops_start.csv'

with open(path, 'w', encoding = 'utf-8-sig') as f:
  stops_start.to_csv(f)

In [393]:
# Adicionando uma coluna apenas com a data para filtrarmos nos Kepler:

stops_start['date'] = pd.to_datetime(stops_start['datetime']).dt.date
stops_start['date'] = stops_start['date'].astype(str)

In [394]:
# Resetando os indexes do pontos de parada

stops_start = stops_start.reset_index(drop=True)
stops_start.head()

geometry  duration_h    length_m   caminhao  \
0  POINT (-46.58513 -23.50948)    8.856944   15.492745  VilaMaria   
1  POINT (-46.57843 -23.47650)    0.333333   23.836020  VilaMaria   
2  POINT (-46.58046 -23.46450)    0.366667  214.530951  VilaMaria   
3  POINT (-46.59782 -23.50340)    1.333333  289.900227  VilaMaria   
4  POINT (-46.56525 -23.52028)    0.733333  104.641575  VilaMaria   

              datetime        date  
0  2022-08-22 00:00:47  2022-08-22  
1  2022-08-22 09:10:12  2022-08-22  
2  2022-08-22 09:36:12  2022-08-22  
3  2022-08-22 10:24:12  2022-08-22  
4  2022-08-22 12:24:12  2022-08-22

In [395]:
stops_start.dtypes

geometry      geometry
duration_h     float64
length_m       float64
caminhao        object
datetime        object
date            object
dtype: object

In [396]:
path = '/content/drive/MyDrive/Projetos/gps_tracking/data/geodata.csv'

with open(path, 'w', encoding = 'utf-8-sig') as f:
  geodata.to_csv(f)

In [397]:
# Resetando os indexes do geodata

geodata = geodata.reset_index(drop=True)
geodata.head()

UltimaComunicacao             DataGPS Velocidade VelocidadeVia Odometro  \
0 2022-08-22 00:00:47 2022-08-22 00:00:47          0            40     9506   
1 2022-08-22 00:00:52 2022-08-22 00:00:52          0            40     9506   
2 2022-08-22 00:00:56 2022-08-22 00:00:56          0            40     9506   
3 2022-08-22 00:22:32 2022-08-22 00:22:32          0            40     9506   
4 2022-08-22 01:02:52 2022-08-22 01:02:52          0            40     9506   

     Ignicao  UF     Cidade     Endereco  Num  Latitude  Longitude SinalModem  \
0  Desligada  SP  São Paulo  Rua Prainha  227 -23.50948 -46.585132     Máximo   
1  Desligada  SP  São Paulo  Rua Prainha  227 -23.50948 -46.585132     Máximo   
2  Desligada  SP  São Paulo  Rua Prainha  227 -23.50948 -46.585132     Máximo   
3  Desligada  SP  São Paulo  Rua Prainha  227 -23.50948 -46.585132     Máximo   
4  Desligada  SP  São Paulo  Rua Prainha  227 -23.50948 -46.585132     Máximo   

                      geometry   caminhao  
0  POINT (-46.58513 -23.50948)  VilaMaria  
1  POINT (-46.58513 -23.50948)  VilaMaria  
2  POINT (-46.58513 -23.50948)  VilaMaria  
3  POINT (-46.58513 -23.50948)  VilaMaria  
4  POINT (-46.58513 -23.50948)  VilaMaria

In [398]:
# Redefinindo o tipo de variavel, pois o keplergl nao aceita datetime.

geodata['UltimaComunicacao'] = geodata['UltimaComunicacao'].astype(str)
geodata['DataGPS'] = geodata['DataGPS'].astype(str)
geodata.dtypes

UltimaComunicacao      object
DataGPS                object
Velocidade             object
VelocidadeVia          object
Odometro               object
Ignicao                object
UF                     object
Cidade                 object
Endereco               object
Num                    object
Latitude               object
Longitude              object
SinalModem             object
geometry             geometry
caminhao               object
dtype: object

In [399]:
# Adicionando uma coluna apenas com a data para filtrar no Kepler:

geodata['data'] = pd.to_datetime(geodata['UltimaComunicacao']).dt.date
geodata['data'] = geodata['data'].astype(str)

In [409]:
# Criando a variavel com pontos geometricos:

servicos['geometry'] = [Point(long, lat) for long, lat in zip(dfServicos['latitude'].to_list(), dfServicos['longitude'].to_list())]

In [410]:
servicos = gpd.GeoDataFrame(dfServicos, crs = CRS.from_epsg('4326'))
servicos.head()

os  fornecimento                                          endereco  \
0   217120589  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
1  2213857848  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
2  2228054536  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
3  2228500845  235219029001   RUA BOA VISTA, 36,  - PQ NOVO MUNDO - SÃO PAULO   
4   217120890  233181989001     RUA TANQUE VELHO, 2093,  - V NIVI - SÃO PAULO   

   data_competencia     data_execucao                         tss  \
0  01/11/2021 06:56  01/11/2021 14:35  DESOBSTRUIR REDE DE ESGOTO   
1  22/04/2022 09:10  23/04/2022 08:19  DESOBSTRUIR REDE DE ESGOTO   
2  23/08/2022 09:40  24/08/2022 08:20  DESOBSTRUIR REDE DE ESGOTO   
3  26/08/2022 13:53  26/08/2022 16:00  DESOBSTRUIR REDE DE ESGOTO   
4  01/11/2021 07:03  01/11/2021 08:55  DESOBSTRUIR REDE DE ESGOTO   

             fornecedor              causa_resultado        pde  latitude  \
0  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  235219029 -46.57382   
1  TECSA SERVIÇOS LTDA.    TRATA-SE DE OUTRO SERVIÇO  235219029 -46.57382   
2  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  235219029 -46.57382   
3  TECSA SERVIÇOS LTDA.    TRATA-SE DE OUTRO SERVIÇO  235219029 -46.57382   
4  TECSA SERVIÇOS LTDA.  DESOBSTRUIDA REDE DE ESGOTO  233181989 -46.58537   

   longitude        data                     geometry  
0 -23.516436  2021-01-11  POINT (-46.57382 -23.51644)  
1 -23.516436  2022-04-23  POINT (-46.57382 -23.51644)  
2 -23.516436  2022-08-24  POINT (-46.57382 -23.51644)  
3 -23.516436  2022-08-26  POINT (-46.57382 -23.51644)  
4 -23.473747  2021-01-11  POINT (-46.58537 -23.47375)

In [402]:
servicos.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Int64Index: 2395 entries, 0 to 2394
Data columns (total 11 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   os                2395 non-null   object 
 1   fornecimento      2395 non-null   object 
 2   endereco          2395 non-null   object 
 3   data_competencia  2395 non-null   object 
 4   data_execucao     2395 non-null   object 
 5   tss               2395 non-null   object 
 6   fornecedor        2395 non-null   object 
 7   causa_resultado   2395 non-null   object 
 8   pde               2395 non-null   int64  
 9   latitude          2395 non-null   float64
 10  longitude         2395 non-null   float64
dtypes: float64(2), int64(1), object(8)
memory usage: 224.5+ KB


In [403]:
# Adicionando uma coluna apenas com a data para filtrar no Kepler:

servicos['data'] = pd.to_datetime(servicos['data_execucao']).dt.date
servicos['data'] = servicos['data'].astype(str)

In [404]:
# Create KeplerGl instance
m = KeplerGl(height=400)

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


In [405]:
m.add_data(stops_start, 'stops')

In [406]:
m.add_data(geodata, 'trajectories')

In [411]:
m.add_data(servicos, 'servicos')

In [412]:
from google.colab import output
output.enable_custom_widget_manager()

In [413]:
m

KeplerGl(data={'stops': {'index': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 2…

In [414]:
m.save_to_html(file_name='tecsa_gps_tracking.html')
m.save_to_html(file_name='tecsa_gps_demo.html', read_only=True)

Map saved to tecsa_gps_tracking.html!
Map saved to tecsa_gps_demo.html!
